In [1]:
import argparse
import nltk
import pandas as pd
import pycrfsuite
import numpy as np
import re
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.preprocessing import MultiLabelBinarizer
from nltk.tokenize import sent_tokenize, word_tokenize, RegexpTokenizer

nltk.download('averaged_perceptron_tagger')

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/markishab/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!


True

In [2]:
recipe_sr = pd.read_pickle('../../data/02_intermediate/recipes_sr_final.pickle')

In [3]:
recipe_sr.columns

Index(['title', 'prep_time', 'cook_time', 'recipe_yield', 'tags',
       'ingredients', 'entire_card', 'recipe_links'],
      dtype='object')

In [4]:
recipe_sr.head()

title   prep_time            cook_time  \
0             Grilled Cheese BLT  10 minutes           10 minutes   
1           Pulled Pork Sandwich  10 minutes  2 hours, 45 minutes   
2  How to Make Bacon in the Oven   5 minutes           20 minutes   
3       Sausage Stuffed Zucchini  15 minutes               1 hour   
4      The Best Dry Rub for Ribs   5 minutes                  NaN   

    recipe_yield                                               tags  \
0   4 sandwiches  'Dinner', 'Lunch', 'Sandwich', 'Favorite Summe...   
1  Serves 6 to 8  'Dinner', 'Sandwich', 'Budget', 'Comfort Food'...   
2      12 strips  'Tips', 'Breakfast and Brunch', 'Baking', 'How...   
3       Serves 4  'Dinner', 'Favorite Summer', 'Make-ahead', 'It...   
4            NaN  'Favorite Fall', 'Favorite Summer', 'Game Day'...   

                                         ingredients  \
0  [8 slices sourdough bread, 4 tablespoon unsalt...   
1  [1 large onion, chopped, 6 garlic cloves, peel...   
2  [12 strips bacon, 1/2 teaspoon ground black pe...   
3  [2 tablespoons extra virgin olive oil, 1/2 pou...   
4  [3/4 cup packed dark brown sugar (or 1/2 cup i...   

                                         entire_card  \
0  ['\n\n                    ', '\n              ...   
1  ['\n\n                    ', '\n              ...   
2  ['\n\n                    ', '\n              ...   
3  ['\n\n                    ', '\n              ...   
4  ['\n\n                    ', '\n              ...   

                                        recipe_links  
0  https://www.simplyrecipes.com/recipes/grilled_...  
1  https://www.simplyrecipes.com/recipes/pulled_p...  
2  https://www.simplyrecipes.com/recipes/how_to_m...  
3  https://www.simplyrecipes.com/recipes/italian_...  
4  https://www.simplyrecipes.com/recipes/the_best...

In [5]:
ingredients_lists = list(recipe_sr.ingredients)

Let's tokenize each ingredient (making sure that the punctuation is gone)

In [6]:
ingredients_lists

[['8 slices sourdough bread',
  '4 tablespoon unsalted butter, at room temperature',
  '8 ounces (2 cups) shredded cheddar cheese',
  '2 slicing tomatoes (such as beefsteak, Brandywine, or Cherokee purple), sliced 1/4-inch thick',
  "8 to 12 slices ', 'cooked bacon",
  '12 leaves butterhead or other crispy lettuce',
  'Kosher salt and black pepper'],
 ['1 large onion, chopped',
  '6 garlic cloves, peeled',
  '1 pickled jalapeño pepper, seeded and chopped',
  '2 teaspoons Chipotle chile powder',
  '1 tablespoon tomato paste',
  '2 tablespoon Dijon mustard',
  '3/4 cup distilled white vinegar',
  '1 teaspoon paprika',
  '1/3 cup ketchup',
  '2 teaspoons Worcestershire sauce',
  '1/4 cup light brown sugar',
  'Salt',
  '1 bay leaf',
  '3 pounds pork butt shoulder roast',
  'Hamburger buns'],
 ['12 strips bacon', '1/2 teaspoon ground black pepper (optional)'],
 ['2 tablespoons extra virgin olive oil',
  '1/2 pound Italian sausage, removed from casing',
  '1 large zucchini, 12 to 14 inches 

In [7]:
# let's tokenize all the words and get rid of punctuation
tokenizer = RegexpTokenizer(r'(\d\/\d |\w+)')
token_sr = []
for recipe in ingredients_lists:
    sub_list = []
    for ingredient in recipe: 
        sub_list.append(tokenizer.tokenize(ingredient))
    token_sr.append(sub_list)

In [8]:
token_sr[5]

[['1', 'tablespoon', 'olive', 'oil'],
 ['1/2 ', 'cup', 'diced', 'white', 'onion'],
 ['1', 'pound', 'ground', 'pork'],
 ['3', 'cloves', 'garlic', 'minced'],
 ['1',
  'tablespoon',
  'grated',
  'fresh',
  'ginger',
  'about',
  '1',
  'inch',
  'peeled'],
 ['1',
  'tablespoon',
  'soy',
  'sauce',
  'use',
  'tamari',
  'to',
  'keep',
  'the',
  'recipe',
  'gluten',
  'free'],
 ['1', 'large', 'carrot', 'shredded'],
 ['1', 'medium', 'cucumber', 'sliced'],
 ['1/3 ', 'cup', 'fresh', 'parsley'],
 ['1/3 ', 'cup', 'fresh', 'basil'],
 ['1/3 ', 'cup', 'fresh', 'mint'],
 ['1', 'cup', 'dried', 'jasmine', 'rice', 'to', 'serve'],
 ['1', 'lime', 'sliced', 'to', 'serve'],
 ['Sweet', 'soy', 'sauce', 'to', 'serve'],
 ['Sesame', 'seeds', 'garnish'],
 ['1', 'pita', 'round'],
 ['2', 'tablespoons', 'Greek', 'yogurt'],
 ['Green', 'leaf', 'lettuce'],
 ['1/3 ', 'cup', 'leftover', 'ginger', 'pork'],
 ['Shredded', 'carrot'],
 ['Sliced', 'cucumber'],
 ['Sriracha', 'optional']]

Let's put this into a form that our crf model can handle

In [9]:
crf_data  = []
index = 0
for recipe in token_sr:
    sub_list = []
    for ingredient in recipe:
        pos = nltk.pos_tag(ingredient)
        sub_list.append((pos))
    crf_data.append(sub_list)
    index = index + 1

In [10]:
crf_data[0][0]

[('8', 'CD'), ('slices', 'NNS'), ('sourdough', 'JJ'), ('bread', 'NN')]

### Let's make some features

In [11]:
# almost perfect but the lsit of lists are whole recipies instead of ingredient lines. 
update_feature = []
for index, recipe in enumerate(crf_data):
    sub_list = []
    for idx, doc in enumerate(recipe):
        sub_sub_list = []
        for i, tup in enumerate(doc):
            word = tup[0]
            postag = tup[1]

            features = [
                'bias',
                'word.lower=' + word.lower(),
                'word[-3:]=' + word[-3:],
                'word[-2:]=' + word[-2:],
                'postag=' + postag,
#                 'index=' + str(index)
            ]
            if i > 0:
                word1 = doc[i-1][0]
                postag1 = doc[i-1][1]
                features.extend([
                    '-1:word.lower=' + word1.lower(),
                    '-1:postag=' + postag1
                ])
            else:
                # Indicate that it is the 'beginning of a document'
                features.append('BOS')

            # Features for words that are not
            # at the end of a document
            if i < len(doc)-1:
                word1 = doc[i+1][0]
                postag1 = doc[i+1][1]
                features.extend([
                    '+1:word.lower=' + word1.lower(),
                    '+1:postag=' + postag1
                ])
            else:
                # Indicate that it is the 'end of a document'
                features.append('EOS')
            sub_list.append(features)
    update_feature.append(sub_list)

In [39]:
def singularize(word):
    """
    A poor replacement for the pattern.en singularize function, but ok for now.
    """

    units = {
        "cups": u"cup",
        "tablespoons": u"tablespoon",
        "teaspoons": u"teaspoon",
        "pounds": u"pound",
        "ounces": u"ounce",
        "cloves": u"clove",
        "sprigs": u"sprig",
        "pinches": u"pinch",
        "bunches": u"bunch",
        "slices": u"slice",
        "grams": u"gram",
        "heads": u"head",
        "quarts": u"quart",
        "stalks": u"stalk",
        "pints": u"pint",
        "pieces": u"piece",
        "sticks": u"stick",
        "dashes": u"dash",
        "fillets": u"fillet",
        "cans": u"can",
        "ears": u"ear",
        "packages": u"package",
        "strips": u"strip",
        "bulbs": u"bulb",
        "bottles": u"bottle"
    }

    if word in units.keys():
        return units[word]
    else:
        return word

In [120]:
def word2features(doc, i):
    word = singularize(doc[i][0])
    postag = doc[i][1]

    # Common features for all words
    features = [
        'bias',
        'word.lower=' + word.lower(),
        'word[-3:]=' + word[-3:],
        'word[-2:]=' + word[-2:],
        'postag=' + postag,
    ]
    if i > 0:
        word1 = doc[i-1][0]
        postag1 = doc[i-1][1]
        features.extend([
            '-1:word.lower=' + word1.lower(),
            '-1:postag=' + postag1
        ])
    else:
        # Indicate that it is the 'beginning of a document'
        features.append('BOS')
    # Features for words that are not
    # at the end of a document
    if i < len(doc)-1:
        word1 = doc[i+1][0]
        postag1 = doc[i+1][1]
        features.extend([
            '+1:word.lower=' + word1.lower(),
            '+1:postag=' + postag1
        ])
    else:
        # Indicate that it is the 'end of a document'
        features.append('EOS')

    return features

In [121]:
# A function for extracting features in documents
def extract_features(doc):
    return [word2features(doc, i) for i in range(len(doc))]

# A function fo generating the list of labels for each document
def get_labels(doc):
    return [label for (token, postag, label) in doc]

In [150]:
crf_data_final = []
for recipe in crf_data:
    X = [extract_features(doc) for doc in recipe]
    crf_data_final.append(X)

In [34]:
tagger = pycrfsuite.Tagger()
tagger.open('../../data/04_models/crf_ing_final.model')

In [161]:
sr_labels = []
for recipe in crf_data_final:
    y_pred = [tagger.tag(xseq) for xseq in recipe]
    sr_labels.append(y_pred)

In [168]:
crf_data_final[0][4]

[['bias',
  'word.lower=8',
  'word[-3:]=8',
  'word[-2:]=8',
  'postag=CD',
  'BOS',
  '+1:word.lower=to',
  '+1:postag=TO'],
 ['bias',
  'word.lower=to',
  'word[-3:]=to',
  'word[-2:]=to',
  'postag=TO',
  '-1:word.lower=8',
  '-1:postag=CD',
  '+1:word.lower=12',
  '+1:postag=CD'],
 ['bias',
  'word.lower=12',
  'word[-3:]=12',
  'word[-2:]=12',
  'postag=CD',
  '-1:word.lower=to',
  '-1:postag=TO',
  '+1:word.lower=slices',
  '+1:postag=NNS'],
 ['bias',
  'word.lower=slice',
  'word[-3:]=ice',
  'word[-2:]=ce',
  'postag=NNS',
  '-1:word.lower=12',
  '-1:postag=CD',
  '+1:word.lower=cooked',
  '+1:postag=VBD'],
 ['bias',
  'word.lower=cooked',
  'word[-3:]=ked',
  'word[-2:]=ed',
  'postag=VBD',
  '-1:word.lower=slices',
  '-1:postag=NNS',
  '+1:word.lower=bacon',
  '+1:postag=NN'],
 ['bias',
  'word.lower=bacon',
  'word[-3:]=con',
  'word[-2:]=on',
  'postag=NN',
  '-1:word.lower=cooked',
  '-1:postag=VBD',
  'EOS']]

In [169]:
sr_labels[0][4]

['qty', 'unit', 'unit', 'unit', 'name', 'name']

In [176]:
for recipe, recipe_label in zip(crf_data_final, sr_labels):
    for ingredient, ingredient_label in zip(recipe, recipe_label):
        for word, word_label in zip(ingredient, ingredient_label):
            print(word[1], ':', word_label)
            print('\n')

word.lower=8 : qty


word.lower=slice : unit


word.lower=sourdough : name


word.lower=bread : name


word.lower=4 : qty


word.lower=tablespoon : unit


word.lower=unsalted : name


word.lower=butter : name


word.lower=at : comment


word.lower=room : comment


word.lower=temperature : comment


word.lower=8 : qty


word.lower=ounce : unit


word.lower=2 : unit


word.lower=cup : unit


word.lower=shredded : name


word.lower=cheddar : name


word.lower=cheese : name


word.lower=2 : qty


word.lower=slicing : name


word.lower=tomatoes : name


word.lower=such : comment


word.lower=as : comment


word.lower=beefsteak : comment


word.lower=brandywine : comment


word.lower=or : comment


word.lower=cherokee : comment


word.lower=purple : comment


word.lower=sliced : comment


word.lower=1 : comment


word.lower=4 : comment


word.lower=inch : comment


word.lower=thick : comment


word.lower=8 : qty


word.lower=to : unit


word.lower=12 : unit


word.lower=slice : unit


word.l


word.lower=nutmeg : name


word.lower=3/4  : qty


word.lower=teaspoon : unit


word.lower=kosher : name


word.lower=salt : name


word.lower=2 : qty


word.lower=1/2  : unit


word.lower=cup : unit


word.lower=milk : name


word.lower=preferably : comment


word.lower=whole : comment


word.lower=1 : qty


word.lower=tablespoon : unit


word.lower=unsalted : name


word.lower=butter : name


word.lower=melted : comment


word.lower=12 : qty


word.lower=ounce : unit


word.lower=mexican : name


word.lower=style : comment


word.lower=chorizo : comment


word.lower=sausage : comment


word.lower=removed : comment


word.lower=from : comment


word.lower=casing : comment


word.lower=if : comment


word.lower=necessary : comment


word.lower=12 : qty


word.lower=large : name


word.lower=eggs : name


word.lower=1/2  : qty


word.lower=teaspoon : unit


word.lower=salt : name


word.lower=1/4  : qty


word.lower=teaspoon : unit


word.lower=pepper : name


word.lower=6 : qty


word



word.lower=teaspoon : unit


word.lower=ground : name


word.lower=pepper : name


word.lower=1/4  : qty


word.lower=cup : unit


word.lower=whipping : name


word.lower=cream : name


word.lower=salt : qty


word.lower=to : name


word.lower=taste : name


word.lower=5 : qty


word.lower=cup : unit


word.lower=water : name


word.lower=4 : qty


word.lower=tablespoon : unit


word.lower=sugar : name


word.lower=3 : qty


word.lower=tablespoon : unit


word.lower=kosher : name


word.lower=salt : name


word.lower=3 : qty


word.lower=bay : name


word.lower=leaves : name


word.lower=broken : comment


word.lower=into : comment


word.lower=piece : comment


word.lower=1/2  : qty


word.lower=teaspoon : unit


word.lower=coriander : name


word.lower=seed : name


word.lower=lightly : comment


word.lower=crushed : comment


word.lower=1 : qty


word.lower=sprig : unit


word.lower=thyme : name


word.lower=4 : qty


word.lower=wide : name


word.lower=strip : name


word.lower=o

word.lower=teaspoon : unit


word.lower=freshly : name


word.lower=ground : name


word.lower=black : name


word.lower=pepper : name


word.lower=1 : qty


word.lower=teaspoon : unit


word.lower=ground : name


word.lower=dry : name


word.lower=mustard : name


word.lower=1/4  : qty


word.lower=teaspoon : unit


word.lower=cayenne : name


word.lower=pepper : name


word.lower=6 : qty


word.lower=pound : unit


word.lower=boneless : name


word.lower=pork : name


word.lower=shoulder : name


word.lower=trimmed : comment


word.lower=of : comment


word.lower=excess : comment


word.lower=fat : comment


word.lower=1 : qty


word.lower=12 : unit


word.lower=ounce : unit


word.lower=bottle : name


word.lower=hard : name


word.lower=apple : name


word.lower=cider : name


word.lower=2 : qty


word.lower=cup : unit


word.lower=apple : name


word.lower=cider : name


word.lower=2 : qty


word.lower=tablespoon : unit


word.lower=tomato : name


word.lower=paste : name


word.l

word.lower=or : comment


word.lower=acini : comment


word.lower=de : comment


word.lower=pepe : comment


word.lower=2 : qty


word.lower=quart : unit


word.lower=chicken : name


word.lower=stock : name


word.lower=1/2  : qty


word.lower=head : name


word.lower=or : comment


word.lower=bunch : comment


word.lower=escarole : comment


word.lower=swiss : comment


word.lower=chard : comment


word.lower=or : comment


word.lower=kale : comment


word.lower=stemmed : comment


word.lower=and : comment


word.lower=cut : comment


word.lower=into : comment


word.lower=1 : comment


word.lower=inch : comment


word.lower=piece : comment


word.lower=1 : qty


word.lower=cup : unit


word.lower=freshly : name


word.lower=grated : name


word.lower=parmesan : name


word.lower=for : comment


word.lower=serving : comment


word.lower=1 : qty


word.lower=pound : unit


word.lower=pork : name


word.lower=loin : name


word.lower=or : name


word.lower=boneless : name


word.lower=

...


word.lower=teaspoon : unit


word.lower=salt : name


word.lower=2 : qty


word.lower=teaspoon : unit


word.lower=dijon : name


word.lower=mustard : name


word.lower=8 : qty


word.lower=ounce : unit


word.lower=225g : name


word.lower=cheddar : name


word.lower=cheese : name


word.lower=grated : comment


word.lower=6 : qty


word.lower=egg : name


word.lower=yolks : name


word.lower=decrease : name


word.lower=to : comment


word.lower=4 : comment


word.lower=egg : comment


word.lower=yolks : comment


word.lower=if : comment


word.lower=you : comment


word.lower=would : comment


word.lower=like : comment


word.lower=it : comment


word.lower=less : comment


word.lower=rich : comment


word.lower=3/4  : qty


word.lower=cup : unit


word.lower=sugar : name


word.lower=decrease : comment


word.lower=to : comment


word.lower=1/2  : comment


word.lower=cup : comment


word.lower=if : comment


word.lower=you : comment


word.lower=would : comment


word.lower=like 



word.lower=water : comment


word.lower=begins : comment


word.lower=to : comment


word.lower=boil : comment


word.lower=remove : comment


word.lower=the : comment


word.lower=pan : comment


word.lower=from : comment


word.lower=heat : comment


word.lower=and : comment


word.lower=let : comment


word.lower=it : comment


word.lower=sit : comment


word.lower=covered : comment


word.lower=for : comment


word.lower=10 : comment


word.lower=12 : comment


word.lower=minutes : comment


word.lower=drain : comment


word.lower=the : comment


word.lower=water : comment


word.lower=from : comment


word.lower=the : comment


word.lower=pan : comment


word.lower=add : comment


word.lower=ice : comment


word.lower=water : comment


word.lower=to : comment


word.lower=cool : comment


word.lower=the : comment


word.lower=eggs : comment


word.lower=let : comment


word.lower=sit : comment


word.lower=a : comment


word.lower=couple : comment


word.lower=minutes : comment


word.lower=4 : qty


word.lower=eggs : name


word.lower=2 : qty


word.lower=teaspoon : unit


word.lower=white : name


word.lower=or : name


word.lower=rice : name


word.lower=vinegar : name


word.lower=2 : qty


word.lower=english : name


word.lower=muffins : name


word.lower=butter : qty


word.lower=blender : qty


word.lower=hollandaise : name


word.lower=10 : qty


word.lower=tablespoon : unit


word.lower=unsalted : name


word.lower=butter : name


word.lower=3 : qty


word.lower=egg : name


word.lower=yolks : comment


word.lower=1 : qty


word.lower=tablespoon : unit


word.lower=lemon : name


word.lower=juice : name


word.lower=1/2  : qty


word.lower=teaspoon : unit


word.lower=salt : name


word.lower=dash : qty


word.lower=of : name


word.lower=cayenne : name


word.lower=or : comment


word.lower=tabasco : comment


word.lower=1 : qty


word.lower=1/4  : unit


word.lower=cup : unit


word.lower=all : name


word.lower=purpose : name


word.lower=flour : na

word.lower=onion : name


word.lower=peeled : comment


word.lower=and : comment


word.lower=chopped : comment


word.lower=1 : qty


word.lower=1/4  : name


word.lower=pound : name


word.lower=600g : name


word.lower=plum : name


word.lower=tomatoes : name


word.lower=peeled : comment


word.lower=and : comment


word.lower=chopped : comment


word.lower=or : comment


word.lower=one : comment


word.lower=14 : comment


word.lower=ounce : comment


word.lower=can : comment


word.lower=of : comment


word.lower=diced : comment


word.lower=tomatoes : comment


word.lower=6 : qty


word.lower=eggs : name


word.lower=salt : qty


word.lower=and : name


word.lower=freshly : name


word.lower=ground : name


word.lower=pepper : name


word.lower=6 : qty


word.lower=egg : name


word.lower=yolks : comment


word.lower=1/3  : qty


word.lower=cup : unit


word.lower=sugar : name


word.lower=3/4  : qty


word.lower=cup : unit


word.lower=marsala : name


word.lower=wine : name




word.lower=taste : comment


word.lower=2 : qty


word.lower=cup : unit


word.lower=wild : name


word.lower=rice : name


word.lower=salt : qty


word.lower=3/4  : qty


word.lower=pound : unit


word.lower=mushrooms : name


word.lower=sliced : comment


word.lower=3 : qty


word.lower=celery : name


word.lower=stalk : name


word.lower=chopped : comment


word.lower=1 : qty


word.lower=medium : name


word.lower=yellow : name


word.lower=or : name


word.lower=white : name


word.lower=onion : name


word.lower=chopped : comment


word.lower=5 : qty


word.lower=tbsp : unit


word.lower=unsalted : name


word.lower=butter : name


word.lower=1 : qty


word.lower=cup : unit


word.lower=walnuts : name


word.lower=1 : qty


word.lower=1/2  : unit


word.lower=cup : unit


word.lower=dried : name


word.lower=cranberries : name


word.lower=1 : qty


word.lower=2 : name


word.lower=tbsp : comment


word.lower=fresh : comment


word.lower=sage : comment


word.lower=minced : comme

Can create a metric of user to purchased item like in movie recommendation system.
implicit feedback recommendation system. (don't have stars or anything. All we have is the fact that they bought this thing onece). We are saying that they bought it so I have some confidence that they like it. 

als recommendations with the carts 

The sticking point is how we get around the recommendation part? don't have actual ratings for things in a cart, all we have is bought or not bought (there is no scale). There could be a million different reasons why you buy something that you don't like. There are algorithms for this (extension of the ALS models. Could start with implicit feedback recommendations using ALS). Look for package that is doing this very quickly /. this one building a model to make predictions. 

Other approaches: don't use the supervised side of things. we just find similarities between carts. Now you can find maybe the top three carts that are most similair to your "new cart". We are assuming that these people have similair tastes to you. And then all of these things might be a good suggestion to me as well. this one we are using huristics tyo try and figure out what is similair. Maybe could even ignore the carts if I go this route. 

**content based recommendations**
**implicit feedback recommendations using ALS**

1. the user says they l ike tomatoes, don't like eggplant, like this. 
1. take that 
---
actually matching things that a person likes to a recipe will be incredibly challenging in and of itself. Deciding on the rules of doing the matching will take time to think about and code it. Example, lety's say I like eggplant and garlic. There are so many recipies with eggplant and garlic.

In [40]:
# update_feature = []
# for index, recipe in enumerate(crf_data):
#     sub_list = []
#     for idx, doc in enumerate(recipe): # Each doc is a recipe sentence in a larger recipe 
#         for i, tup in enumerate(doc):
#             word = singularize(tup[0])
#             postag = tup[1]

#             features = [
#                 'bias',
#                 'word.lower=' + word.lower(),
#                 'word[-3:]=' + word[-3:],
#                 'word[-2:]=' + word[-2:],
#                 'postag=' + postag,
#             ]
#             if i > 0:
#                 word1 = doc[i-1][0]
#                 postag1 = doc[i-1][1]
#                 features.extend([
#                     '-1:word.lower=' + word1.lower(),
#                     '-1:postag=' + postag1
#                 ])
#             else:
#                 # Indicate that it is the 'beginning of a document'
#                 features.append('BOS')
#             # Features for words that are not
#             # at the end of a document
#             if i < len(doc)-1:
#                 word1 = doc[i+1][0]
#                 postag1 = doc[i+1][1]
#                 features.extend([
#                     '+1:word.lower=' + word1.lower(),
#                     '+1:postag=' + postag1
#                 ])
#             else:
#                 # Indicate that it is the 'end of a document'
#                 features.append('EOS')
#             ####################################################
#             sub_list.append(features)
#     update_feature.append(sub_list)